# Notebook para gerar os datasets de treinamento do CRF e para aplicação da supervisão fraca

In [2]:
import pandas as pd
import nltk

Ao carregar o csv pelo pandas especifique o data class das colunas. No nosso caso todas são String, então:

     dtype=str

In [3]:
data = pd.read_csv('/home/lucelia_vieira/Experimentos/ner/CSVs/DODFCorpus_contratos_licitacoes_v1.csv', dtype=str)

Para o iob_transformer fazer a correlação ato-entidades_correspondentes é necessário ter uma coluna id_ato, que junte o id do dodf e o id da relação específica.

Mas para que funcione corretamente as colunas id_dodf e id_rel devem ser do tipo String, conforme abaixo: 

 1   id_dodf       30382 non-null  object
 
 3   id_rel        30382 non-null  object

In [4]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 41044 entries, 0 to 41043
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   Unnamed: 0.1  41044 non-null  object
 1   Unnamed: 0    41044 non-null  object
 2   id_dodf       41044 non-null  object
 3   tipo_rel      41044 non-null  object
 4   id_rel        41044 non-null  object
 5   anotador_rel  41044 non-null  object
 6   tipo_ent      41044 non-null  object
 7   id_ent        41044 non-null  object
 8   anotador_ent  41044 non-null  object
 9   offset        41044 non-null  object
 10  length        41044 non-null  object
 11  texto         41044 non-null  object
 12  id_ato        41044 non-null  object
dtypes: object(13)
memory usage: 4.1+ MB


In [5]:
data['id_ato'] = data['id_dodf'] + '-' + data['id_rel']
data

Unnamed: 0.1 Unnamed: 0        id_dodf                 tipo_rel id_rel  \
0                0          0  12_22.11.2018      REL_AVISO_LICITACAO    R21   
1                1          1  12_22.11.2018      REL_AVISO_LICITACAO    R21   
2                2          2  12_22.11.2018      REL_AVISO_LICITACAO    R21   
3                3          3  12_22.11.2018      REL_AVISO_LICITACAO    R21   
4                4          4  12_22.11.2018      REL_AVISO_LICITACAO    R21   
...            ...        ...            ...                      ...    ...   
41039        41054      41054            638  REL_SUSPENSAO_LICITACAO     R7   
41040        41055      41055            638  REL_SUSPENSAO_LICITACAO     R7   
41041        41056      41056            638  REL_SUSPENSAO_LICITACAO     R7   
41042        41057      41057            638  REL_SUSPENSAO_LICITACAO     R7   
41043        41058      41058            638  REL_SUSPENSAO_LICITACAO     R7   

            anotador_rel                    tipo_ent id_ent  \
0      anotador_50435513        modalidade_licitacao      1   
1      anotador_50435513            numero_licitacao      2   
2      anotador_50435513  valor_estimado_contratacao      6   
3      anotador_50435513     data_abertura_licitacao      7   
4      anotador_50435513             sistema_compras      8   
...                  ...                         ...    ...   
41039  anotador_14379604                processo_gdf    258   
41040  anotador_14379604             orgao_licitante    255   
41041  anotador_14379604            objeto_licitacao   3902   
41042  anotador_14379604             orgao_licitante   3206   
41043  anotador_14379604            nome_responsavel   3901   

            anotador_ent  offset length  \
0      anotador_50435513  432851     17   
1      anotador_50435513  432872      8   
2      anotador_50435513  433432     10   
3      anotador_50435513  433599     10   
4      anotador_50435513  433716     21   
...                  ...     ...    ...   
41039  anotador_14379604  210132     22   
41040  anotador_14379604  210158     63   
41041  anotador_14379604  210322    367   
41042  anotador_14379604  210631     58   
41043  anotador_14379604  210768     25   

                                                   texto             id_ato  
0                                      PREGAO ELETRONICO  12_22.11.2018-R21  
1                                               116/2018  12_22.11.2018-R21  
2                                             767.907,37  12_22.11.2018-R21  
3                                             20/11/2018  12_22.11.2018-R21  
4                                  www.compras.df.gov.br  12_22.11.2018-R21  
...                                                  ...                ...  
41039                             04012-00000112/2022-79             638-R7  
41040  Secretaria de Estado de Trabalho do Distrito F...             638-R7  
41041  Registro de Preços para contratação de empresa...             638-R7  
41042  Secretaria de Estado do Trabalho Distrito Fede...             638-R7  
41043                          JUNILMA OLIVEIRA FERREIRA             638-R7  

[41044 rows x 13 columns]

Checando o tipo da coluna id_ato

In [6]:

#type(data.at[30379, 'id_ato'])

Checando o formato do id_ato

In [7]:

#data.at[30377, 'id_ato']

In [8]:
result = data.groupby('tipo_rel')['id_ato'].nunique()
print(result.sort_values(ascending=False))


tipo_rel
REL_ADITAMENTO_CONTRATO     1537
REL_EXTRATO_CONTRATO        1537
REL_AVISO_LICITACAO          638
REL_SUSPENSAO_LICITACAO       68
REL_ANUL_REVOG_LICITACAO      46
REL_EXTRATO_CONVENIO          24
Name: id_ato, dtype: int64


Com os dados certinhos, podemos fazer uso do iob_transformer normalmente, mas antes vamos relizar alguns filtros.

O primeiro filtro a ser aplicado é pelo tipo de ATO:

In [9]:
data.tipo_rel.value_counts()

REL_EXTRATO_CONTRATO        20750
REL_ADITAMENTO_CONTRATO     11796
REL_AVISO_LICITACAO          7413
REL_SUSPENSAO_LICITACAO       497
REL_ANUL_REVOG_LICITACAO      350
REL_EXTRATO_CONVENIO          238
Name: tipo_rel, dtype: int64

É utilizados uns ilocs no código do transformer, então por via das dúvidas é bom dar um reset_index nos dataframes filtrados:

In [10]:
tipo_ato = data.loc[data['tipo_rel'] == 'REL_EXTRATO_CONTRATO'].reset_index(drop=True)
#tipo_ato.to_csv("/home/lucelia_vieira/Experimentos/ner/CSVs/REL_EXTRATO_CONTRATO_COMPLETO.csv")
tipo_ato


Unnamed: 0.1 Unnamed: 0        id_dodf              tipo_rel id_rel  \
0              179        179  12_22.11.2018  REL_EXTRATO_CONTRATO     R1   
1              180        180  12_22.11.2018  REL_EXTRATO_CONTRATO     R1   
2              181        181  12_22.11.2018  REL_EXTRATO_CONTRATO     R1   
3              182        182  12_22.11.2018  REL_EXTRATO_CONTRATO     R1   
4              183        183  12_22.11.2018  REL_EXTRATO_CONTRATO     R1   
...            ...        ...            ...                   ...    ...   
20745        41046      41046            638  REL_EXTRATO_CONTRATO    R85   
20746        41047      41047            638  REL_EXTRATO_CONTRATO    R85   
20747        41048      41048            638  REL_EXTRATO_CONTRATO    R85   
20748        41049      41049            638  REL_EXTRATO_CONTRATO    R85   
20749        41050      41050            638  REL_EXTRATO_CONTRATO    R85   

            anotador_rel             tipo_ent id_ent       anotador_ent  \
0      anotador_33117818      numero_contrato    355  anotador_33117818   
1      anotador_33117818         processo_gdf    354  anotador_33117818   
2      anotador_33117818    orgao_contratante    356  anotador_33117818   
3      anotador_33117818  entidade_contratada    357  anotador_33117818   
4      anotador_33117818       valor_contrato    359  anotador_33117818   
...                  ...                  ...    ...                ...   
20745  anotador_33117818       valor_contrato   1184  anotador_33117818   
20746  anotador_33117818    programa_trabalho   1188  anotador_33117818   
20747  anotador_33117818     natureza_despesa   1189  anotador_33117818   
20748  anotador_33117818         nota_empenho   1191  anotador_33117818   
20749  anotador_33117818    vigencia_contrato   1185  anotador_33117818   

       offset length                                              texto  \
0      556566      7                                            45/2018   
1      556584     22                             00070-00016600/2018-76   
2      556617      9                                          SEAGRI/DF   
3      556630     56  CIMAG  COMERCIO DE\nIMPLEMENTOS E MAQUINAS AGR...   
4      557492      9                                          39.600,00   
...       ...    ...                                                ...   
20745  209063     10                                         547.811,64   
20746  209204     21                              08.244.6228.4232.0002   
20747  209230     11                                        33.90.39.81   
20748  209283     11                                        2022NE00130   
20749  209476    209  O contrato terá vigência de 12 (doze) meses, a...   

                 id_ato  
0      12_22.11.2018-R1  
1      12_22.11.2018-R1  
2      12_22.11.2018-R1  
3      12_22.11.2018-R1  
4      12_22.11.2018-R1  
...                 ...  
20745           638-R85  
20746           638-R85  
20747           638-R85  
20748           638-R85  
20749           638-R85  

[20750 rows x 13 columns]

In [11]:
#apenas para rodar o iob com spacy
#csv_reader = pd.read_csv("/home/lucelia_vieira/Experimentos/ner/CSVs/REL_EXTRATO_CONTRATO_COMPLETO.csv", nrows=2000)

In [12]:
tipo_ato.tipo_ent.value_counts()

orgao_contratante           2034
numero_contrato             1700
entidade_contratada         1576
processo_gdf                1549
EXTRATO_CONTRATO            1542
objeto_contrato             1534
vigencia_contrato           1484
valor_contrato              1407
fonte_recurso               1319
programa_trabalho           1287
nota_empenho                1270
data_assinatura_contrato    1108
natureza_despesa            1083
unidade_orcamentaria        1019
cnpj_entidade_contratada     402
nome_responsavel             182
codigo_siggo                 150
cnpj_orgao_contratante       104
Name: tipo_ent, dtype: int64

In [13]:
# CODIGO RESPONSAVEL PELA LIMPEZA DO TEXTO DA BASE OURO
#tipo_ato_2 = tipo_ato.copy()
#tipo_ato_2 = csv_reader.copy()
#tipo_ato_2.texto = tipo_ato_2.texto.str.replace("\n", " ")
#tipo_ato_2.texto = tipo_ato_2.texto.str.replace("  ", " ")

Alguns atos possuem entidades rotuladas incorretamente, ou que, a quantide de rótulos não seja representativo. Nesse caso, sugere-se remover essas entidades do dataset.

In [14]:
#l = ['codigo_siggo','numero_convenio','nome_responsavel']
#l = ['codigo_siggo','numero_convenio','nome_responsavel']

#tipo_ato = tipo_ato.loc[~tipo_ato.tipo_ent.isin(l)]

Após ter aplicado todos os filtros no dataset, podemos realizar o transfomer e converter para o formato IOB.

In [15]:
# return_df=False para retornar atos e labels, ou  return_df=True para retornar dataset
from iob_transformer import iob_transformer
iob = iob_transformer('id_ato','texto','tipo_ent', keep_punctuation=False, return_df=False)

/home/lucelia_vieira/Experimentos/venv/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2022-09-22 01:38:12.172887: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-09-22 01:38:12.176452: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-09-22 01:38:12.176885: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:975] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero


In [16]:
atos, labels = iob.transform(tipo_ato)

In [17]:
atos

[['EXTRATO',
  'DO',
  'CONTRATO',
  'PARA',
  'AQUISICAO',
  'DE',
  'BENS',
  'No',
  '45/2018',
  'PROCESSO',
  ':',
  '00070-00016600/',
  '2018-76',
  '.',
  'Partes',
  ':',
  'SEAGRI',
  '/',
  'DF',
  'e',
  'CIMAG',
  'COMERCIO',
  'DE',
  'IMPLEMENTOS',
  'E',
  'MAQUINAS',
  'AGRICOLAS',
  'LTDA',
  '.',
  'Objeto',
  ':',
  'O',
  'Contrato',
  'tem',
  'por',
  'objeto',
  'a',
  'aquisicao',
  'dos',
  'seguintes',
  'itens',
  ':',
  'Item',
  '20',
  ':',
  'Quantidade',
  '03',
  '(',
  'tres',
  ')',
  '.',
  'GRADE',
  'ARADORA',
  'CONTROLE',
  'R',
  'E',
  'M',
  'O',
  'TO',
  ',',
  'com',
  '14',
  'discos',
  'de',
  '26',
  'polegadas',
  'de',
  'diametro',
  'e',
  '06',
  'mm',
  'de',
  'espessura',
  'minima',
  ',',
  'mancais',
  'de',
  'rolamento',
  'com',
  'lubrificacao',
  'permanente',
  'em',
  'banho',
  'de',
  'oleo',
  ',',
  'ou',
  'a',
  'graxa',
  ',',
  'espacamento',
  'minimo',
  'entre',
  'os',
  'discos',
  'de',
  '230',
  'mm',


In [18]:
#Cria uma Lista 
atos_list = []
for i in atos:
   if not isinstance(i, list):
      atos_list.append(i)
   else:
      for j in i:
        atos_list.append(j)

len(atos_list)

366452

In [19]:
df = pd.DataFrame(atos_list,columns=['Texto']) 
df.to_csv('./CSVs/atos.csv')

In [20]:
#Cria uma Lista 
label_list = []
for i in labels:
   if not isinstance(i, list):
      label_list.append(i)
   else:
      for j in i:
        label_list.append(j)

len(label_list)

366452

In [21]:
#iob_dataset = iob_transformer('id_ato', 'texto',
#           'tipo_ent', keep_punctuation=False, return_df=True)


In [22]:
#dataset_iob = iob_dataset.transform(tipo_ato)
#dataset_iob

## Separate train and test splits (in order)

Aqui usamos trains_test_split do sklearn para separar os conjuntos de treino e teste de forma randômica e sistematizada.

In [23]:
from sklearn.model_selection import train_test_split
# 80% treino, 20% teste
#x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=None, shuffle=False)
#random_state: the seed number to be passed to the shuffle operation, thus making the experiment reproducible.
x_train_s, x_test_s, y_train_s, y_test_s = train_test_split(atos, labels, test_size=0.2, random_state=None, shuffle=True)
print( 'x_train',len(x_train_s),'\n','x_test',len(x_test_s),'\n','total atos',len(atos))

x_train 1229 
 x_test 308 
 total atos 1537


In [24]:
#x_test_s

In [39]:
#Cria uma Lista com o x_test
x_test_list = []
for i in x_test_s:
   if not isinstance(i, list):
      x_test_list.append(i)
   else:
      for j in i:
        x_test_list.append(j)

len(x_test_list)

74902

In [26]:
#x_test_list

In [27]:
y_test_list = []
for i in y_test_s:
   if not isinstance(i, list):
      y_test_list.append(i)
   else:
      for j in i:
       y_test_list.append(j)

len(y_test_list)

74902

In [28]:
simbolos_pontuacao = ["'", '"', ",", ".", "!", ":", ";", '#', '@', '-']
if x_test_s in simbolos_pontuacao:
    x_test_texto = list(map(''.join, x_test_s))
else:
    x_test_texto = list(map(' '.join, x_test_s))         
x_test_texto

['EXTRATO DO CONTRATO Nº 23/2021 - FUNP / DF - SIGGO 044966 Processo : 04026-00039462/ 2021-02 - SECRETARIA DE ESTADO DE ADMINISTRAÇÃO PENITENCIÁRIA - SEAPE / DF , na qualidade de CONTRATANTE e a empresa RMG TECNOLOGIA INTEGRADO EIRELI - CNPJ : 30.517.827/ 0001-38 , na qualidade de CONTRATADA . DO OBJETO : 08 ( oito ) NOTEBOOKS , com as especificações constantes do item 3 da Ata de Registro de Preços n ° 09/ 2021-SEAPE ; 165 ( cento e sessenta e cinco ) MONITORES , com as especificações constantes do item 2 da Ata de Registro de Preços n ° 09/ 2021-SEAPE ; e 165 ( cento e sessenta e cinco ) COMPUTADORES , com as especificações constantes do item 1 da Ata de Registro de Preços n ° 09/ 2021-SEAPE , conforme especifica o Edital de PREGÃO ELETRÔNICO Nº 009/2021 - SEAPE / DF , Autorização de Despesa e Empenho , Ato Autorizativo , Declaração de Orçamento e Nota técnica nº 283 - SEAPE / AJL . DO VALOR : o valor do contrato é de R$ 1.049.290,00 ( um milhão , quarenta e nove mil duzentos e nove

In [35]:
import re

df2 =[]

for i in x_test_list:
    i = re.sub('xx[a-z]{1,10}', '', i)
    aux = ''.join(i)
    #print(aux)
    df2.append(aux)

df2

['EXTRATO',
 'DO',
 'CONTRATO',
 'Nº',
 '23/2021',
 '-',
 'FUNP',
 '/',
 'DF',
 '-',
 'SIGGO',
 '044966',
 'Processo',
 ':',
 '04026-00039462/',
 '2021-02',
 '-',
 'SECRETARIA',
 'DE',
 'ESTADO',
 'DE',
 'ADMINISTRAÇÃO',
 'PENITENCIÁRIA',
 '-',
 'SEAPE',
 '/',
 'DF',
 ',',
 'na',
 'qualidade',
 'de',
 'CONTRATANTE',
 'e',
 'a',
 'empresa',
 'RMG',
 'TECNOLOGIA',
 'INTEGRADO',
 'EIRELI',
 '-',
 'CNPJ',
 ':',
 '30.517.827/',
 '0001-38',
 ',',
 'na',
 'qualidade',
 'de',
 'CONTRATADA',
 '.',
 'DO',
 'OBJETO',
 ':',
 '08',
 '(',
 'oito',
 ')',
 'NOTEBOOKS',
 ',',
 'com',
 'as',
 'especificações',
 'constantes',
 'do',
 'item',
 '3',
 'da',
 'Ata',
 'de',
 'Registro',
 'de',
 'Preços',
 'n',
 '°',
 '09/',
 '2021-SEAPE',
 ';',
 '165',
 '(',
 'cento',
 'e',
 'sessenta',
 'e',
 'cinco',
 ')',
 'MONITORES',
 ',',
 'com',
 'as',
 'especificações',
 'constantes',
 'do',
 'item',
 '2',
 'da',
 'Ata',
 'de',
 'Registro',
 'de',
 'Preços',
 'n',
 '°',
 '09/',
 '2021-SEAPE',
 ';',
 'e',
 '165',
 '(',

In [ ]:
""" simbolos_pontuacao = ["'", '"', ",", ".", "!", ":", ";", '#', '@', '-']
texto = "EXTRATO DO CONTRATO PARA AQUISIÇÃO DE BENS PELO DISTRITO FEDERAL Nº 08/ 2022-SEJUS - SIGGO Nº 045498 Processo : 00400-00013706/ 2021-99 . Das Partes : SECRETARIA DE ESTADO DE JUSTIÇA E CIDADANIA DO DF X DANTON GABRIEL S. DE S. SILVA ME . Do Objeto : Aquisição de material : caixa acústica : caixa acústica ativa 15 1000w ; e microfone de lapela com as seguintes especificações : transdutor do tipo condensador ; padrão polar omnidirecional ; resposta de frequência 50 hz - 18khz ; sensibilidade de circuito aberto : -54 db . Do Valor do Contrato : O valor total do Contrato é de R$ 1.684,00 ( um mil seiscentos e oitenta e quatro reais ) , devendo a importância ser atendida à conta de dotações orçamentárias consignadas no orçamento corrente Lei Orçamentária nº 6.482 , de 09 de Janeiro de 2020 . DA DOTAÇÃO ORÇAMENTÁRIA : I - Unidade Orçamentária : 44.101 ; II - Programa de Trabalho 14.243.6211.2412. 0003-MANUTENÇÃO E FUNCIONAMENTO DO CENTRO DE ATENDIMENTO INTEGRADO À CRIANÇAS VÍTIMAS DE VIOLÊNCIA SEXUAL-DF.OCA ; III - Natureza da Despesa : 44.90.52 ; IV - Fonte de Recurso : 732020590 . O empenho inicial é de R$ 1.684,00 ( um mil seiscentos e oitenta e quatro reais ) , conforme Nota de Empenho nº 2022NE00394 , emitida em 11/03/2022 , sob o evento nº 400091 , na modalidade Ordinário . DATA DE ASSINATURA : 14/03/2022 . SIGNATÁRIOS : Pelo DISTRITO FEDERAL : JAIME SANTANA DE SOUSA , na qualidade de Secretário-Executivo , da Secretaria de Estado de Justiça do Distrito Federal . Pela CONTRATADA : DANTON GABRIEL SIMPLICIO DE SALES SILVA , na qualidade de Representante Legal ."

def to_regex(s):
    r=''
    if (re.search("\s+", texto)):
	    r=re.sub(" ","", texto)
    return r
print(to_regex(texto))
 """

' simbolos_pontuacao = ["\'", \'"\', ",", ".", "!", ":", ";", \'#\', \'@\', \'-\']\ntexto = "EXTRATO DO CONTRATO PARA AQUISIÇÃO DE BENS PELO DISTRITO FEDERAL Nº 08/ 2022-SEJUS - SIGGO Nº 045498 Processo : 00400-00013706/ 2021-99 . Das Partes : SECRETARIA DE ESTADO DE JUSTIÇA E CIDADANIA DO DF X DANTON GABRIEL S. DE S. SILVA ME . Do Objeto : Aquisição de material : caixa acústica : caixa acústica ativa 15 1000w ; e microfone de lapela com as seguintes especificações : transdutor do tipo condensador ; padrão polar omnidirecional ; resposta de frequência 50 hz - 18khz ; sensibilidade de circuito aberto : -54 db . Do Valor do Contrato : O valor total do Contrato é de R$ 1.684,00 ( um mil seiscentos e oitenta e quatro reais ) , devendo a importância ser atendida à conta de dotações orçamentárias consignadas no orçamento corrente Lei Orçamentária nº 6.482 , de 09 de Janeiro de 2020 . DA DOTAÇÃO ORÇAMENTÁRIA : I - Unidade Orçamentária : 44.101 ; II - Programa de Trabalho 14.243.6211.2412. 000

In [ ]:
""" texto = "EXTRATO DO CONTRATO PARA AQUISIÇÃO DE BENS PELO DISTRITO FEDERAL Nº 08/ 2022-SEJUS - SIGGO Nº 045498 Processo : 00400-00013706/ 2021-99 . Das Partes : SECRETARIA DE ESTADO DE JUSTIÇA E CIDADANIA DO DF X DANTON GABRIEL S. DE S. SILVA ME . Do Objeto : Aquisição de material : caixa acústica : caixa acústica ativa 15 1000w ; e microfone de lapela com as seguintes especificações : transdutor do tipo condensador ; padrão polar omnidirecional ; resposta de frequência 50 hz - 18khz ; sensibilidade de circuito aberto : -54 db . Do Valor do Contrato : O valor total do Contrato é de R$ 1.684,00 ( um mil seiscentos e oitenta e quatro reais ) , devendo a importância ser atendida à conta de dotações orçamentárias consignadas no orçamento corrente Lei Orçamentária nº 6.482 , de 09 de Janeiro de 2020 . DA DOTAÇÃO ORÇAMENTÁRIA : I - Unidade Orçamentária : 44.101 ; II - Programa de Trabalho 14.243.6211.2412. 0003-MANUTENÇÃO E FUNCIONAMENTO DO CENTRO DE ATENDIMENTO INTEGRADO À CRIANÇAS VÍTIMAS DE VIOLÊNCIA SEXUAL-DF.OCA ; III - Natureza da Despesa : 44.90.52 ; IV - Fonte de Recurso : 732020590 . O empenho inicial é de R$ 1.684,00 ( um mil seiscentos e oitenta e quatro reais ) , conforme Nota de Empenho nº 2022NE00394 , emitida em 11/03/2022 , sob o evento nº 400091 , na modalidade Ordinário . DATA DE ASSINATURA : 14/03/2022 . SIGNATÁRIOS : Pelo DISTRITO FEDERAL : JAIME SANTANA DE SOUSA , na qualidade de Secretário-Executivo , da Secretaria de Estado de Justiça do Distrito Federal . Pela CONTRATADA : DANTON GABRIEL SIMPLICIO DE SALES SILVA , na qualidade de Representante Legal ."
texto.rstrip
texto """

' texto = "EXTRATO DO CONTRATO PARA AQUISIÇÃO DE BENS PELO DISTRITO FEDERAL Nº 08/ 2022-SEJUS - SIGGO Nº 045498 Processo : 00400-00013706/ 2021-99 . Das Partes : SECRETARIA DE ESTADO DE JUSTIÇA E CIDADANIA DO DF X DANTON GABRIEL S. DE S. SILVA ME . Do Objeto : Aquisição de material : caixa acústica : caixa acústica ativa 15 1000w ; e microfone de lapela com as seguintes especificações : transdutor do tipo condensador ; padrão polar omnidirecional ; resposta de frequência 50 hz - 18khz ; sensibilidade de circuito aberto : -54 db . Do Valor do Contrato : O valor total do Contrato é de R$ 1.684,00 ( um mil seiscentos e oitenta e quatro reais ) , devendo a importância ser atendida à conta de dotações orçamentárias consignadas no orçamento corrente Lei Orçamentária nº 6.482 , de 09 de Janeiro de 2020 . DA DOTAÇÃO ORÇAMENTÁRIA : I - Unidade Orçamentária : 44.101 ; II - Programa de Trabalho 14.243.6211.2412. 0003-MANUTENÇÃO E FUNCIONAMENTO DO CENTRO DE ATENDIMENTO INTEGRADO À CRIANÇAS VÍTIMAS

In [ ]:
x_test_texto

['EXTRATO DO CONTRATO Nº 44/2021 , NOS TERMOS DO PADRÃO Nº 07/2002 AQUISIÇÃO DE BENS Processo : 052-00010597/ 2020-10 PARTES : Distrito Federal / Polícia Civil X Inbraterrestre Indústria e Comércio de Materiais de Segurança Ltda . FUNDAMENTAÇÃO LEGAL : Ata de Registro de Preços nº 25/ 2020-SEGEN / MJSP ( 63215752 ) , resultante do Pregão Eletrônico nº 20/ 2020-SEGEN / MJSP ( 53358003 ) , do Termo de Referência ( 54516712 ) , da Proposta da Empresa ( 60615504 ) , da Nota Técnica 13 ( 64547637 ) , da Manifestação 4122 ( 64343082 ) , dos Despachos ( 64350178 e 64664436 ) , nos exatos termos do artigo 2º , inciso V , do Decreto Distrital nº 39.103/2018 , e artigo 2º , inciso IV , do Decreto n ° 7.892/2013 . OBJETO : Aquisição de 685 ( seiscentos e oitenta e cinco ) unidades de Colete a Prova de Bala Nível III-A , Tamanho M , Masculino ; 689 ( seiscentos e oitenta e nove ) unidades de Colete a Prova de Bala Nível III-A , Tamanho G , Masculino ; 127 ( cento e vinte e sete ) unidades de Colet

In [ ]:
#CODIGO RESPONSAVEL PELA LIMPEZA DO TEXTO DA BASE OURO
""" import re

df1 =[]

for i in x_test_texto:
    i = i.replace("\n", " ")
    i = re.sub('xx[a-z]{1,10}', '', i)
    #i = i.replace(r"xx[a-z]{1,10}","")
    aux = ' '.join(i.split())
    #print(aux)
    df1.append(aux) """

' import re\n\ndf1 =[]\n\nfor i in x_test_texto:\n    i = i.replace("\n", " ")\n    i = re.sub(\'xx[a-z]{1,10}\', \'\', i)\n    #i = i.replace(r"xx[a-z]{1,10}","")\n    aux = \' \'.join(i.split())\n    #print(aux)\n    df1.append(aux) '

In [ ]:
#x_test para rodar o supervisao fraca
df = pd.DataFrame(x_test_texto,columns=['Texto']) 
df.to_csv('/home/lucelia_vieira/Experimentos/ner/CSVs/Extrato_Contrato_Split_3_x_test_texto.csv')

In [ ]:
# converting Split Test to CSV file
# labels para validação do x_test
df = pd.DataFrame(x_test_list, columns=['Texto']) 
df.to_csv('/home/lucelia_vieira/Experimentos/ner/CSVs/Extrato_Contrato_Split_3_x_test.csv')

In [ ]:
df = pd.DataFrame(y_test_list, columns=['Texto']) 
df.to_csv('/home/lucelia_vieira/Experimentos/ner/CSVs/Extrato_Contrato_Split_3_y_test.csv')

In [ ]:
""" resultados = []
for ato_gold, label_gold in zip(atos, labels):
    tupla=(ato_gold,label_gold)
    resultados.append(tupla)
print(resultados) """

' resultados = []\nfor ato_gold, label_gold in zip(atos, labels):\n    tupla=(ato_gold,label_gold)\n    resultados.append(tupla)\nprint(resultados) '

In [ ]:
# CODIGO RESPONSAVEL PELA LIMPEZA DO TEXTO DA BASE OURO
#x_test_list = [elemento for elemento in resultados if elemento.strip()]